In [63]:
import numpy as np
import pandas as pd
import plotly.express as px

In [64]:
data = np.load('/home/theorcos239/spatiotemporal_analysis/data/metr_la_new.npz')

In [65]:
data['edges']

array([[  0,  37],
       [  0,  54],
       [  0, 116],
       ...,
       [206, 155],
       [206, 159],
       [206, 163]], dtype=int32)

In [66]:
dataset = data['targets']
dataset_size = len(dataset)

In [67]:
for i in range(0, len(dataset)):
    for j in range(0, len(dataset[i])):
        if np.isnan(dataset[i][j]):
            dataset[i][j] = dataset[max(i -1, 0)][j]

In [68]:
import torch 
from torch.utils.data import TensorDataset, DataLoader


In [69]:
device = "cuda" if torch.cuda.is_available() else "cpu"
device

'cpu'

In [70]:
train_size = int(0.75 * dataset_size)
vercity = 0
train_dataset = dataset[:train_size, vercity]
test_dataset = dataset[train_size:, vercity]

In [71]:
coef = 10
X_train = [train_dataset[i - coef: i] for i in range(coef, train_size)]
X_train = torch.tensor(X_train).to(device)
print(X_train)

tensor([[64.3750, 62.6667, 64.0000, 64.0000],
        [62.6667, 64.0000, 64.0000, 64.0000],
        [64.0000, 64.0000, 64.0000, 57.3333],
        ...,
        [66.0000, 66.0000, 66.0000, 66.0000],
        [66.0000, 66.0000, 66.0000, 66.0000],
        [66.0000, 66.0000, 66.0000, 66.0000]])


In [72]:
y_train = train_dataset[coef: train_size]
y_train = torch.tensor(y_train).to(device)

print(X_train.shape, y_train.shape)
print(y_train)

torch.Size([25700, 4]) torch.Size([25700])
tensor([64.0000, 57.3333, 66.5000,  ..., 66.0000, 66.0000, 66.0000])


In [73]:
train_data_set = TensorDataset(X_train, y_train)
train_dataloader = DataLoader(train_data_set,
                        shuffle = True,
                        batch_size = 8,
                        )

In [74]:
from torch import nn

model = nn.Linear(coef, 1)
model.to(device)

loss_fn = nn.L1Loss()

In [90]:
optimizer = torch.optim.Adam(params = model.parameters(), lr = 0.00000001)

In [91]:
from tqdm import tqdm

In [92]:
epochs = 100

losses = []

for i in tqdm(range(epochs)):
    for x, y in train_dataloader:
        y_pred = model(x).flatten().to(device)
        loss = loss_fn(y_pred, y).to(device)
        losses.append(loss.item())
        optimizer.zero_grad()
        loss.backward()
        optimizer.step()


  0%|          | 0/100 [00:00<?, ?it/s]

100%|██████████| 100/100 [02:31<00:00,  1.52s/it]


In [93]:
px.line(y = np.array(losses))

In [94]:
np.array(losses).mean()

2.3649352464813553